&emsp; &emsp; &emsp; &emsp; &emsp; &emsp; &emsp; &emsp; &emsp; &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp;  &emsp; **OLAP Constructs - ROLLUP, CUBE, and GROUPING SETS**


ROLLUP, CUBE and GROUPING SETS are SQL aggregation extensions that allow her to perform multiple GROUP BY operations in the same statement. With these new SQL constructs GROUPTING SETS, ROLLUP and CUBE, he can avoid complex data processing code in the applications and also help improve your performance.


Miguel has recently been tasked to perform multi-dimensional analysis on supplier data. He needs to write complex aggregation logic for finding totals, sub total of supplier account balances at nation level, region level and for each of the combinations


## Pre-requisties

1. Create Amazon Redshift cluster - https://docs.aws.amazon.com/redshift/latest/gsg/rs-gsg-launch-sample-cluster.html
    
    Note: You can also demo this on Redshift Serverless
2. Ensure you setup an IAM role as default IAM role.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/default-iam-role.html#managing-iam-role-console) for instructions.

In [0]:
--Miguel needs to create the table structures that will hold the sales data. Create a supplier sample table and insert sample data.

DROP TABLE IF EXISTS supp_sample;
CREATE TABLE IF NOT EXISTS supp_sample (
        supp_id integer, 
        region_nm char(25), 
        nation_nm char(25), 
        acct_balance numeric(12,2)
        );

In [0]:
-- Insret sample sales data

INSERT INTO public.supp_sample (supp_id,region_nm,nation_nm,acct_balance) 
VALUES  
(90470,'AFRICA                   ','KENYA                    ',1745.57),  
(99910,'AFRICA                   ','ALGERIA                  ',3659.98),  
(26398,'AMERICA                  ','UNITED STATES            ',2575.77),  
(43908,'AMERICA                  ','CANADA                   ',1428.27),  
(3882,'AMERICA                  ','UNITED STATES            ',7932.67),  
(42168,'ASIA                     ','JAPAN                    ',343.34),  
(68461,'ASIA                     ','CHINA                    ',2216.11),  
(89676,'ASIA                     ','INDIA                    ',4160.75),  
(52670,'EUROPE                   ','RUSSIA                   ',2469.40),  
(32190,'EUROPE                   ','RUSSIA                   ',1119.55),  
(19587,'EUROPE                   ','GERMANY                  ',9904.98),  
(1134,'MIDDLE EAST              ','EGYPT                    ',7977.48),  
(35213,'MIDDLE EAST              ','EGYPT                    ',737.28),  
(36132,'MIDDLE EAST              ','JORDAN                   ',5052.87);

Let us start by first reviewing the sample data before running the SQLs using GROUPING SETS, ROLLUP, and CUBE extensions. It has list of suppliers , region, nation and their account balances.

In [0]:
select * from supp_sample;

**GROUPING SETS**
Group data multiple different ways. GROUPING SETS can be used instead of performing multiple select queries with different GROUP BY keys and merge (i.e., Union) their results.  Below query groups data by both region_nm and nation_nm.In this section, we will show how to find out 

- account balances aggregated for each region 

- account balances aggregated for each nation 

- merge results of both aggregations

by running single SQL statement using GROUPING SETS.

In [0]:
SELECT region_nm, nation_nm, sum(acct_balance) as total_balance
FROM supp_sample
GROUP BY GROUPING SETS (region_nm, nation_nm);

**ROLLUP**
Group data by particular columns and get extra rows that represent the subtotals. ROLLUP assumes a hierarchy among the GROUP BY columns.

In this section, we will show how to find out 

- account balances for each combination of region_nm and nation_nm 

- rolled up account balances for each region_nm 

- rolled up account balances for all regionsin single SQL statement using ROLLUP. 

The rows with a value for region_nm and NULL value for nation_nm represent the subtotals for the region (marked in green). The rows with NULL value for both region_nm and nation_nm has the grand total—the rolled-up account balances for all regions (marked in red).

In [0]:
SELECT region_nm, nation_nm, sum(acct_balance) as total_balance
FROM supp_sample
GROUP BY ROLLUP (region_nm, nation_nm)
ORDER BY region_nm,nation_nm;

Similar to ROLLUP, CUBE will group data by particular columns and get extra rows that represent the subtotals. Also, it will generate subtotals for all combinations of grouping columns.

In this section, we will show how to find out 

- account balance sub totals for each nation_nm 

- account balance sub totals for each region_nm 

- account balance sub totals for each group of region_nm and nation_nmcombination  

- Overall total account balance for all regions

in single SQL statement using CUBEYou can see the subtotals at region level . These subtotal records are the same records generated by ROLLUP. Additionally, CUBE generated subtotals for each nation_nm . Finally, you can also see the grand total for all three regions mentioned in the query.

In [0]:
SELECT region_nm, nation_nm, sum(acct_balance) as total_balance
FROM supp_sample
WHERE region_nm in ('AFRICA','AMERICA','ASIA') 
GROUP BY CUBE(region_nm, nation_nm)ORDER BY region_nm, nation_nm;

NULL is a valid value in a column that participates in a GROUPING SET/ROLLUP/CUBE and it is not aggregated with the NULL values added explicitly to the result set to satisfy the schema of returning tuples. Below is an example with a ROLLUP, where the NULL value of an input column and the NULL values added explicitly to the output are highlighted in green and red, respectively.

In [0]:
-- Create example orders table

CREATE TABLE orders(item_no int,description varchar,quantity int);

In [0]:
--Insert sample order records
INSERT INTO orders(item_no,description,quantity) 
VALUES(101,'apples',10),(102,null,15),(103,'banana',20);

In [0]:
--View the data before start working on SQL constructs

SELECT * FROM orders;

Run rollup query on the data with NULLs. 

Observe that there will be two output rows for item_no 102 in below SQL output.

In [0]:
SELECT item_no, description, sum(quantity) 
FROM orders 
GROUP BY ROLLUP(item_no, description) ORDER BY 1,2;

## Cleanup

Please delete the Redshift cluster to avoid unnecessary costs. https://docs.aws.amazon.com/redshift/latest/mgmt/managing-clusters-console.html#delete-cluster

Thank you for using this notebook.  Please share your feedback to redshift-specialists-amer@amazon.com